## Process earnings reports data from saved pickle

E. Quinn 12/20/2020

## Import standard python datascience packages

In [1]:
import sys
import math
import re
import copy
import numpy as np
import scipy as sc
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
import pickle
%matplotlib inline

In [2]:
from datetime import datetime, timedelta, date
from datascience import *
import uuid
import random

### Import custom SC classes

In [3]:
sys.path.append("/home/gquinn/EG/school_committee/egsc/py_egsc")

In [4]:
from cba_salaries import Teacher_salaries 
from payperiod import Payperiod
from ucoa_labels import UCOA_labels
from eg_acct_codes import EG_acct_codes
from pay_check import Pay_check, Check_lineitem
from person import Person
from scenario import Scenario

In [5]:
ts = Teacher_salaries()
help(ts)

Help on Teacher_salaries in module cba_salaries object:

class Teacher_salaries(builtins.object)
 |  Methods defined here:
 |  
 |  __init__(self)
 |      Initialize self.  See help(type(self)) for accurate signature.
 |  
 |  decode_earnings(self, check_date, rate, in_earnings, obj)
 |  
 |  get_cba_matrix(self)
 |  
 |  get_future_code_from_code(self, code, incr)
 |      Returns CBA salary given step code for FY2013-FY2022.
 |  
 |  get_future_salary_from_code(self, code, incr)
 |      Returns CBA salary given step code for FY2013-FY2022.
 |  
 |  get_salary(self, fyear, step, col)
 |      Returns CBA salary given fiscal year, column, and step for FY2013-FY2022.
 |  
 |  get_salary_from_code(self, code)
 |      Returns CBA salary given step code for FY2013-FY2022.
 |  
 |  ----------------------------------------------------------------------
 |  Data descriptors defined here:
 |  
 |  __dict__
 |      dictionary for instance variables (if defined)
 |  
 |  __weakref__
 |      list o

### Show the directory we are running in

In [6]:
!pwd

/home/gquinn/EG/school_committee/finance_subcommittee/notebooks


### Load RIDE UCOA labels 

In [7]:
UCOA_labels = UCOA_labels()
    
#help(UCOA_labels)

### EG accounting codes class

provides descriptions for EG accounting codes and mapping to UCOA codes

In [8]:
EG_acct_codes = EG_acct_codes()
    
#help(EG_acct_codes)

### Load teacher salary matrix code

In [9]:
teacher_salary_matrix = Teacher_salaries()
    
#help(teacher_salary_matrix)

### Load serialized people object produced from earnings report

In [10]:
#Load data (deserialize)
with open('../../finance_subcommittee/people_12_22_2020.pkl', 'rb') as handle:
    people = pickle.load(handle)
    
len(people)

898

In [16]:
first_syear = {}

for name in people.keys():
    pp = people[name].get_payperiods()
    for syear in pp.keys():
        for seq in pp[syear].keys():
            syseq = pp[syear][seq].get_school_year_seq()
            paydat = pp[syear][seq].get_payday()
            chks = pp[syear][seq].get_checks()
            for chk in chks.keys():
                itms = chks[chk].get_items()
                for itm in itms.keys():
                    accd = itms[itm].get_acct_desc()
                    earn = itms[itm].get_earnings()
                    print(name,syear,seq,syseq,paydat,chk,itm,accd,earn)
    
    
    
first_syear

ELSON, SUSAN E 2013-2014 24 24 2014-07-25 248415 1 K Frenchtown 2967.85
ELSON, SUSAN E 2013-2014 24 24 2014-07-25 248415 2 K Frenchtown 2967.85
ELSON, SUSAN E 2013-2014 25 25 2014-07-25 248415 1 K Frenchtown 2967.85
ELSON, SUSAN E 2013-2014 25 25 2014-07-25 248415 2 K Frenchtown 2967.85
ELSON, SUSAN E 2013-2014 26 26 2014-08-08 248434 1 K Frenchtown 2967.85
ELSON, SUSAN E 2014-2015 1 1 2014-08-22 249658 1 K Frenchtown 3027.19
ELSON, SUSAN E 2014-2015 2 2 2014-09-05 249827 1 K Frenchtown 3027.19
ELSON, SUSAN E 2014-2015 3 3 2014-09-19 250036 1 K Frenchtown 3027.19
ELSON, SUSAN E 2014-2015 4 4 2014-10-03 250252 1 K Frenchtown 3027.19
ELSON, SUSAN E 2014-2015 4 4 2014-10-03 250252 2 (no description) 15.0
ELSON, SUSAN E 2014-2015 5 5 2014-10-17 250482 1 K Frenchtown 3027.19
ELSON, SUSAN E 2014-2015 5 5 2014-10-17 250482 2 (no description) 7.5
ELSON, SUSAN E 2014-2015 6 6 2014-10-31 250739 1 K Frenchtown 3027.19
ELSON, SUSAN E 2014-2015 7 7 2014-11-14 250966 1 K Frenchtown 3027.19
ELSON, SU

RAKOVIC, EMILY E 2016-2017 7 7 2016-11-11 2129249 1 K Frenchtown 2382.73
RAKOVIC, EMILY E 2016-2017 8 8 2016-11-25 2130072 1 K Frenchtown 2382.73
RAKOVIC, EMILY E 2016-2017 9 9 2016-12-09 2130818 1 K Frenchtown 2382.73
RAKOVIC, EMILY E 2016-2017 10 10 2016-12-23 2131451 1 K Frenchtown 2382.73
RAKOVIC, EMILY E 2016-2017 11 11 2017-01-06 2132083 1 K Frenchtown 2382.73
RAKOVIC, EMILY E 2016-2017 12 12 2017-01-20 2132793 1 K Frenchtown 2382.73
RAKOVIC, EMILY E 2016-2017 13 13 2017-02-03 2133415 1 K Frenchtown 2382.73
RAKOVIC, EMILY E 2016-2017 14 14 2017-02-17 2134026 1 K Frenchtown 2382.73
RAKOVIC, EMILY E 2016-2017 15 15 2017-03-03 2134648 1 K Frenchtown 2382.73
RAKOVIC, EMILY E 2016-2017 16 16 2017-03-17 2135267 1 K Frenchtown 2382.73
RAKOVIC, EMILY E 2016-2017 17 17 2017-03-31 2135895 1 K Frenchtown 2382.73
RAKOVIC, EMILY E 2016-2017 18 18 2017-04-14 2136537 1 K Frenchtown 2382.73
RAKOVIC, EMILY E 2016-2017 19 19 2017-04-28 2137189 1 K Frenchtown 2382.73
RAKOVIC, EMILY E 2016-2017 20 2

DEPASQUALE, HELEN L 2015-2016 15 15 2016-03-04 2115852 1 K MDBK 3034.54
DEPASQUALE, HELEN L 2015-2016 16 16 2016-03-18 2116447 1 K MDBK 3034.54
DEPASQUALE, HELEN L 2015-2016 17 17 2016-04-01 2117054 1 K MDBK 3034.54
DEPASQUALE, HELEN L 2015-2016 18 18 2016-04-15 2117803 1 K MDBK 3034.54
DEPASQUALE, HELEN L 2015-2016 19 19 2016-04-29 2118403 1 K MDBK 3034.54
DEPASQUALE, HELEN L 2015-2016 20 20 2016-05-13 2119063 1 K MDBK 3034.54
DEPASQUALE, HELEN L 2015-2016 21 21 2016-05-27 2120627 1 K MDBK 3034.54
DEPASQUALE, HELEN L 2015-2016 22 22 2016-06-10 2121382 1 K MDBK 3034.54
DEPASQUALE, HELEN L 2015-2016 22 22 2016-06-10 2121160 1 K MDBK 2187.5
DEPASQUALE, HELEN L 2015-2016 23 23 2016-06-24 2121608 1 K MDBK 3034.54
DEPASQUALE, HELEN L 2015-2016 24 24 2016-07-22 2122893 1 K MDBK 3034.54
DEPASQUALE, HELEN L 2015-2016 24 24 2016-07-22 2122893 2 K MDBK 3034.54
DEPASQUALE, HELEN L 2015-2016 25 25 2016-07-22 2122893 1 K MDBK 3034.54
DEPASQUALE, HELEN L 2015-2016 25 25 2016-07-22 2122893 2 K MDBK 3

DEPASQUALE, HELEN L 2019-2020 4 4 2019-09-27 2178991 1 K MDBK 3164.88
DEPASQUALE, HELEN L 2019-2020 4 4 2019-09-27 2178991 2 Other Compensation-MDBK 15.0
DEPASQUALE, HELEN L 2019-2020 5 5 2019-10-11 2179680 1 K MDBK 3164.88
DEPASQUALE, HELEN L 2019-2020 6 6 2019-10-25 2180368 1 K MDBK 3164.88
DEPASQUALE, HELEN L 2019-2020 6 6 2019-10-25 2180368 2 Other Compensation-MDBK 15.0
DEPASQUALE, HELEN L 2019-2020 7 7 2019-11-08 2181072 1 K MDBK 3164.88
DEPASQUALE, HELEN L 2019-2020 8 8 2019-11-22 2181756 1 K MDBK 3164.88
DEPASQUALE, HELEN L 2019-2020 9 9 2019-12-06 2182556 1 K MDBK 3164.88
DEPASQUALE, HELEN L 2019-2020 10 10 2019-12-20 2183247 1 K MDBK 3164.88
DEPASQUALE, HELEN L 2019-2020 10 10 2019-12-20 2183247 2 Other Compensation-MDBK 30.0
DEPASQUALE, HELEN L 2019-2020 11 11 2020-01-03 2183941 1 K MDBK 3164.88
DEPASQUALE, HELEN L 2019-2020 12 12 2020-01-17 2184605 1 K MDBK 3164.88
DEPASQUALE, HELEN L 2019-2020 13 13 2020-01-31 2185275 1 K MDBK 3164.88
DEPASQUALE, HELEN L 2019-2020 14 14 20

MATTOX, JENNIFER L 2018-2019 4 4 2018-09-28 2162178 2 Other Compensation-MDBK 30.0
MATTOX, JENNIFER L 2018-2019 5 5 2018-10-12 2162809 1 K MDBK 3279.0
MATTOX, JENNIFER L 2018-2019 6 6 2018-10-26 2163429 1 K MDBK 3279.0
MATTOX, JENNIFER L 2018-2019 7 7 2018-11-09 2164059 1 K MDBK 3279.0
MATTOX, JENNIFER L 2018-2019 7 7 2018-11-09 2164059 2 Other Compensation-MDBK 37.5
MATTOX, JENNIFER L 2018-2019 8 8 2018-11-23 2164708 1 K MDBK 3279.0
MATTOX, JENNIFER L 2018-2019 9 9 2018-12-07 2165377 1 K MDBK 3279.0
MATTOX, JENNIFER L 2018-2019 10 10 2018-12-21 2166039 1 K MDBK 3279.0
MATTOX, JENNIFER L 2018-2019 11 11 2019-01-04 2166660 1 K MDBK 3279.0
MATTOX, JENNIFER L 2018-2019 12 12 2019-01-18 2167267 1 K MDBK 3279.0
MATTOX, JENNIFER L 2018-2019 13 13 2019-02-01 2167894 1 K MDBK 3279.0
MATTOX, JENNIFER L 2018-2019 14 14 2019-02-15 2168504 1 K MDBK 3279.0
MATTOX, JENNIFER L 2018-2019 14 14 2019-02-15 2168504 2 K MDBK 30.0
MATTOX, JENNIFER L 2018-2019 15 15 2019-03-01 2169133 1 K MDBK 3279.0
MATTOX

...

AYDIN, KOCAK R 2019-2020 1 1 2019-08-16 278242 1 (no description) 240.0
BILODEAU, ERIN E 2019-2020 1 1 2019-08-16 278209 1 SPED Hanaford 2775.81
BILODEAU, ERIN E 2019-2020 2 2 2019-08-30 2177387 1 SPED Hanaford 2775.81
BILODEAU, ERIN E 2019-2020 3 3 2019-09-13 2178054 1 SPED Hanaford 2775.81
BILODEAU, ERIN E 2019-2020 4 4 2019-09-27 2178728 1 SPED Hanaford 2775.81
BILODEAU, ERIN E 2019-2020 5 5 2019-10-11 2179419 1 SPED Hanaford 2775.81
BILODEAU, ERIN E 2019-2020 6 6 2019-10-25 2180104 1 SPED Hanaford 2775.81
BILODEAU, ERIN E 2019-2020 7 7 2019-11-08 2180808 1 SPED Hanaford 2775.81
BILODEAU, ERIN E 2019-2020 7 7 2019-11-08 2180808 2 Teacher Subs Hanaford 30.0
BILODEAU, ERIN E 2019-2020 8 8 2019-11-22 2181492 1 SPED Hanaford 2775.81
BILODEAU, ERIN E 2019-2020 8 8 2019-11-22 2181492 2 Teacher Subs Hanaford 15.0
BILODEAU, ERIN E 2019-2020 9 9 2019-12-06 2182292 1 SPED Hanaford 2775.81
BILODEAU, ERIN E 2019-2020 10 10 2019-12-20 2182981 1 SPED Hanaford 2775.81
BILODEAU, ERIN E 2019-2020 11

VARONE, LESLIE F 2019-2020 6 6 2019-10-25 279118 2 Long Term Subs Eldredge 150.0
VARONE, LESLIE F 2019-2020 7 7 2019-11-08 279276 1 Long Term Subs Eldredge 1000.0
ZUBIAGO, ANTONIA M 2019-2020 3 3 2019-09-13 278601 1 Teacher Subs Eldredge 75.0
ZUBIAGO, ANTONIA M 2019-2020 4 4 2019-09-27 2179050 1 Teacher Subs Eldredge 150.0
ZUBIAGO, ANTONIA M 2019-2020 4 4 2019-09-27 2179050 2 Teacher Subs MDBK 112.5
ZUBIAGO, ANTONIA M 2019-2020 5 5 2019-10-11 2179739 1 Teacher Subs Eldredge 150.0
ZUBIAGO, ANTONIA M 2019-2020 5 5 2019-10-11 2179739 2 Teacher Subs Cole 37.5
ZUBIAGO, ANTONIA M 2019-2020 5 5 2019-10-11 2179739 3 Teacher Subs Hanaford 75.0
ZUBIAGO, ANTONIA M 2019-2020 5 5 2019-10-11 2179739 4 (no description) 65.63
ZUBIAGO, ANTONIA M 2019-2020 7 7 2019-11-08 2181132 1 Teacher Subs Eldredge 150.0
ZUBIAGO, ANTONIA M 2019-2020 7 7 2019-11-08 2181132 2 Teacher Subs MDBK 150.0
ZUBIAGO, ANTONIA M 2019-2020 7 7 2019-11-08 2181132 3 Teacher Subs Hanaford 37.5
ZUBIAGO, ANTONIA M 2019-2020 7 7 2019-1

ALTIERI, JOHN R 2019-2020 18 18 2020-04-10 281064 1 (no description) 3843.36
MAGUIRE, MEGHANN K 2019-2020 2 2 2019-08-30 278420 1 (no description) 400.0
TURCHETTA, SARAH M 2019-2020 2 2 2019-08-30 278427 1 (no description) 200.0
IMBRIGLIO, JESSICA E 2019-2020 2 2 2019-08-30 278419 1 (no description) 300.0
WEHR, CALLAN F 2019-2020 2 2 2019-08-30 278429 1 (no description) 200.0
HULING, CATHERINE F 2019-2020 2 2 2019-08-30 278418 1 (no description) 200.0
MCLAUGHLIN, MARY MARTHA E 2019-2020 15 15 2020-02-28 280714 1 Nurse Subs Cole 100.0
MCLAUGHLIN, MARY MARTHA E 2019-2020 15 15 2020-02-28 280714 2 Nurse Subs EGHS 100.0
MCLAUGHLIN, MARY MARTHA E 2019-2020 16 16 2020-03-13 2187406 1 Nurse Subs MDBK 200.0
MCLAUGHLIN, MARY MARTHA E 2019-2020 17 17 2020-03-27 2188088 1 Nurse Subs MDBK 200.0
MCLAUGHLIN, MARY MARTHA E 2019-2020 17 17 2020-03-27 2188088 2 Nurse Subs Hanaford 100.0
GILDAY, MEAGAN T 2019-2020 6 6 2019-10-25 279109 1 Nurse Subs Cole 75.0
GILDAY, MEAGAN T 2019-2020 6 6 2019-10-25 279

RAO, JOHN 2019-2020 10 10 2019-12-20 2183328 1 Custodian Subs EGHS 504.0
RAO, JOHN 2019-2020 15 15 2020-02-28 2186741 1 Custodian Subs EGHS 562.0
RAO, JOHN 2019-2020 15 15 2020-02-28 2186741 2 Custodian Subs Hanaford 562.0
RAO, JOHN 2019-2020 17 17 2020-03-27 2188115 1 Custodian Subs EGHS 449.6
SMITH-HAZZARD, ZOE M 2018-2019 25 25 2019-07-19 2175906 1 Custodian Subs Cole 899.2
SMITH-HAZZARD, ZOE M 2018-2019 25 25 2019-07-19 2175906 2 Custodian Subs Cole 899.2
SMITH-HAZZARD, ZOE M 2018-2019 26 26 2019-08-02 2176365 1 Custodian Subs Cole 1011.6
SMITH-HAZZARD, ZOE M 2018-2019 24 24 2019-07-19 2175906 1 Custodian Subs Cole 899.2
SMITH-HAZZARD, ZOE M 2018-2019 24 24 2019-07-19 2175906 2 Custodian Subs Cole 899.2
SMITH-HAZZARD, ZOE M 2019-2020 1 1 2019-08-16 2177039 1 Custodian Subs EGHS 449.6
SMITH-HAZZARD, ZOE M 2019-2020 2 2 2019-08-30 2177701 1 Custodian Subs EGHS 786.8
JOSLOFF, LEAH E 2018-2019 25 25 2019-07-19 2175897 1 Custodian Subs Cole 786.8
JOSLOFF, LEAH E 2018-2019 25 25 2019-07-

{}